<a href="https://colab.research.google.com/github/LeonardoCamargoRossato/MetCompB/blob/main/Resolucao_Trabalho2__SistemaMassaMola/Resolucao_Trabalho2.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
# pip install plotly
# pip install numpy
# pip install math
# pip install time

In [ ]:
import numpy as np
from math import *
import plotly.graph_objects as go

In [ ]:
def plota_gráfico(list_t, list_x, nome):
    fig = go.Figure(data=go.Scatter(x=list_t, y=list_x))
    fig.update_layout(title='Sistema Massa-Mola via '+nome,
                      xaxis_title='Tempo', yaxis_title='Valor',
                      width=800, height=400, template='seaborn')
    fig.show()

## Solução exata: Problema Massa-Mola  ou MHS em 1D

#### Problema Geral a ser resolvido:

$$\frac{d^2 x}{dt^2} = - w^2 x    \;\;\;\;\;\; onde,  \;\;\;\;  w = \sqrt{\frac{k}{m}} $$
---
___
#### Solução Analítica (usando técnicas de resolução de EDO):
$$ x(t) = A\cos(wt + \alpha_0)  \;\;\;\; onde,   \;\;\;\; \alpha_0 =  \;"Fase \; Inicial"\;; \;\;\; A = \;"Amplitude" $$

In [ ]:
# Condições Iniciais
k = 1; m = 1; fase = 0; A = 1

w = sqrt(k/m)
# x = A*cos(w*t + fase)

list_t = np.linspace(0,10,1000)
list_x = [ A*cos(w*t + fase) for t in list_t ]   #"Técnica usada": list comprehension

plota_gráfico(list_t, list_x, 'Solução Analítica')

---
---
### Começa aqui a resolução do trabalho 2.    ** A função analítica plotada é só por questão de didática.

---
---
---
---
---
---
---
---
---
---

# Soluções Numéricas (Aproximadas) do Sistema massa-mola 1D

###### --> Basicamente resolver numericamente a Equação Diferencial:

$$\frac{d^2 x}{dt^2} = - w^2 x    \;\;\;\;\;\; onde,  \;\;\;\;  w = \sqrt{\frac{k}{m}} $$
---

##### Reajustando equações e reduzindo a ordem, obtemos:
---

$$
\begin{equation*}
    \left\{
        \begin{matrix}
           \frac{d^2 x}{dt^2} = \frac{d v}{dt} = - w^2 x := a(x,k,m)\\
            \frac{d x}{dt} = v \\
        \end{matrix}
    \right.
\end{equation*}  
$$
---

usando a seguinte redução --> $\frac{dv}{dt} = a = - \frac{kx}{m} \;\; $ mais $\;\; \frac{dx}{dt} = v$

## Verlet

In [ ]:
# Função aceleração Massa-Mola
def a(x,k,m):
    return -k*x/m

def Verlet_massa_mola(dt,k,m,xold,x,v,t,tf):
    np = int((tf-t)/dt)
    list_x = [x]; list_v = [v]; list_t = [t]

    xnew = x + v*dt
    for i in range(1,np):
        t = i*dt
        xnew = 2*x - xold + a(x,k,m)*dt**2
        v = (xnew - xold)/(2*dt)

        list_x.append(xnew); list_v.append(v); list_t.append(t)
        xold = x; x = xnew
    return list_x, list_v, list_t

## Velocity Verlet

In [ ]:
def VelocityVerlet_massa_mola(dt,k,m,x,v,t,tf):
    np = int((tf-t)/dt);
    list_x = [x]; list_v = [v]; list_t = [t]

    ax = a(x,k,m)
    for i in range(1,np):
        t = i*dt
        v = v + ax*dt/2
        x = x + v*dt
        ax = a(x,k,m)
        v = v + ax*dt/2

        list_x.append(x); list_v.append(v); list_t.append(t)
    return list_x, list_v, list_t

## Runge Kutta 2 (RK2)

In [ ]:
def RK2_massa_mola(dt,k,m,x,v,t,tf):
    np = int((tf-t)/dt);
    list_x = [x]; list_v = [v]; list_t = [t]

    for i in range(1,np):
        t = i*dt

        x2 = x + v*dt/2
        v2 = v + a(x,k,m)*dt/2

        x = x + v2*dt
        v = v + a(x2,k,m)*dt
        list_x.append(x); list_v.append(v); list_t.append(t)
    return list_x, list_v, list_t

## Runge Kutta 4  (RK4)

In [ ]:
def RK4_massa_mola(dt,k,m,x,v,t,tf):
    np = int((tf-t)/dt);
    list_x = [x]; list_v = [v]; list_t = [t]

    for i in range(1,np):
        t = i*dt

        a1 = a(x,k,m); v1 = v

        x2 = x + v1*dt/2
        v2 = v + a1*dt/2;  a2 = a(x2,k,m)

        x3 = x + v2*dt/2
        v3 = v + a2*dt/2;  a3 = a(x3,k,m)

        x4 = x + v3*dt/2
        v4 = v + a3*dt/2;  a4 = a(x4,k,m)

        x = x + ( v1+ 2*v2 + 2*v3 + v4 )*dt/6
        v = v + ( a1+ 2*a2 + 2*a3 + a4 )*dt/6
        list_x.append(x); list_v.append(v); list_t.append(t)
    return list_x, list_v, list_t

## Compara Erro dos métodos usando Energia:
___
___

$$ Erro(\Delta t) = \sqrt{ \frac{ \sum_{i=0}^{i=n} (E_0 - E(t_i))^2 } { NE_0^2 } } $$

In [ ]:
# Condições Iniciais
dt = 0.001; k = 1; m = 1; x = 1; v = 0; t = 0; tf = 6
xold = 0.999998; x_verlet = 0.999999

# Chama as funções dos Métodos: Verlet, Vel.Verlet, RK2 e RK4
list_x1, list_v1, list_t1 = Verlet_massa_mola(dt,k,m,xold,x_verlet,v,t,tf)
list_x3, list_v3, list_t3 = VelocityVerlet_massa_mola(dt,k,m,x,v,t,tf)
list_x4, list_v4, list_t4 = RK2_massa_mola(dt,k,m,x,v,t,tf)
list_x5, list_v5, list_t5 = RK4_massa_mola(dt,k,m,x,v,t,tf)

# Função que calcula Erro (pela Energia)
def calcula_erro_pela_Energia(list_x,k):
    E0 = k*(list_x[0]**2)/2; somatorio = 0; erro = []; cont = 0
    for x in list_x:
        cont += 1 #Contador
        E = k*(x**2)/2
        somatorio = somatorio + ( (E0 - E)**2 )
        erro.append(sqrt( somatorio / (cont*E0**2)  ))
    return erro

# Atribui resultados do Cálculo do erro em listas
erro_1 = calcula_erro_pela_Energia(list_x1,k)
erro_3 = calcula_erro_pela_Energia(list_x3,k)
erro_4 = calcula_erro_pela_Energia(list_x4,k)
erro_5 = calcula_erro_pela_Energia(list_x5,k)

# Compara métodos
---
---
#### Figura 1: Comparação de Verlet com RK2

In [ ]:
# Plot do gráfico comparado
fig = go.Figure()
fig.add_trace(go.Scatter(x=list_t1, y=erro_1, mode='lines', name='Verlet'))
fig.add_trace(go.Scatter(x=list_t3, y=erro_3, mode='lines', name='Velocity Verlet'))
fig.add_trace(go.Scatter(x=list_t4, y=erro_4, mode='lines', name='RK2'))

fig.update_layout(title='IGURA 1: Compara métodos pela Energia p/ Sistema Massa-Mola',
                  xaxis_title='Tempo', yaxis_title='Erro energia',
                  width=800, height=600, template='seaborn', hovermode="y unified",
                  xaxis_type='log',yaxis_type='log')
fig.show()


#### Figura 2: Comparação de Verlet com RK4

In [ ]:
# Plot do gráfico comparado
fig = go.Figure()
fig.add_trace(go.Scatter(x=list_t1, y=erro_1, mode='lines', name='Verlet'))
fig.add_trace(go.Scatter(x=list_t3, y=erro_3, mode='lines', name='Velocity Verlet'))
fig.add_trace(go.Scatter(x=list_t5, y=erro_5, mode='lines', name='RK4'))

fig.update_layout(title='FIGURA 2: Compara métodos pela Energia p/ Sistema Massa-Mola',
                  xaxis_title='Tempo', yaxis_title='Erro energia',
                  width=800, height=600, template='seaborn', hovermode="y unified",
                  xaxis_type='log',yaxis_type='log')
fig.show()

---
---
---
---
---
---
A resolução do Trabalho acaba aqui.
---
A partir daqui tem algumas outras observações e códigos alternativos

---
---
---
---
---
---
---
---
---
---
---
---



# Compara métodos  (Parte Gráfica):

#### Figura 3: Comparação de Verlet com RK4 e RK2

In [ ]:
# Cálcula solução analítica p/ Sistema Massa mola
fase = 0; A = 1; w = sqrt(k/m);
list_t = np.linspace(0,10,1000)
list_x = [ A*cos(w*t + fase) for t in list_t ]

# Plot do gráfico comparado
fig = go.Figure()
fig.add_trace(go.Scatter(x=list_t1, y=erro_1, mode='lines', name='Verlet'))
# fig.add_trace(go.Scatter(x=list_t2, y=list_x2, mode='lines', name='Leap-Frog'))
fig.add_trace(go.Scatter(x=list_t3, y=erro_3, mode='lines', name='Velocity Verlet'))
fig.add_trace(go.Scatter(x=list_t4, y=erro_4, mode='lines', name='RK2'))
fig.add_trace(go.Scatter(x=list_t5, y=erro_5, mode='lines', name='RK4'))

fig.update_layout(title='Compara métodos pela Energia: Sistema Massa-Mola',
                  xaxis_title='Tempo', yaxis_title='Erro energia',
                  width=800, height=600, template='seaborn', hovermode="y unified",
                  xaxis_type='log',yaxis_type='log')
fig.show()

#### Problema Geral a ser resolvido:

$$\frac{d^2 x}{dt^2} = - w^2 x    \;\;\;\;\;\; onde,  \;\;\;\;  w = \sqrt{\frac{k}{m}} $$
---

In [ ]:
# Plot do gráfico comparado
fig = go.Figure()
fig.add_trace(go.Scatter(x=list_t, y=list_x, mode='lines', name='Solução Analítica'))
fig.add_trace(go.Scatter(x=list_t1, y=list_x1, mode='lines', name='Verlet'))
fig.add_trace(go.Scatter(x=list_t3, y=list_x3, mode='lines', name='Velocity Verlet'))
fig.add_trace(go.Scatter(x=list_t4, y=list_x4, mode='lines', name='RK2'))
fig.add_trace(go.Scatter(x=list_t5, y=list_x5, mode='lines', name='RK4'))

fig.update_layout(title='Compara métodos: Sistema Massa-Mola',
                  xaxis_title='Tempo', yaxis_title='Valor',
                  width=1000, height=800, template='seaborn')
fig.update_layout(hovermode="y unified")
fig.show()


### Compara métodos (Tempo de execução):

In [ ]:
import time

'''
 Usei a função time() para salvar a informação do tempo antes e depois de chamar cada método
 e com isso estimar uma comparação da "velocidade" dos mesmos.

 # Tempo cálculo método : = fim - ini
'''

ini1 = time.time(); list_x1, list_v1, list_t1 = Verlet_massa_mola(dt,k,m,xold,x,v,t,tf);    fim1 = time.time()
ini3 = time.time(); list_x3, list_v3, list_t3 = VelocityVerlet_massa_mola(dt,k,m,x,v,t,tf); fim3 = time.time()
ini4 = time.time(); list_x4, list_v4, list_t4 = RK2_massa_mola(dt,k,m,x,v,t,tf);            fim4 = time.time()
ini5 = time.time(); list_x5, list_v5, list_t5 = RK4_massa_mola(dt,k,m,x,v,t,tf);            fim5 = time.time()

print('Tempo Verlet:          ', round(fim1-ini1,6))
print('Tempo Velocity Verlet: ', round(fim3-ini3,6))
print('Tempo RK2:             ', round(fim4-ini4,6))
print('Tempo RK4:             ', round(fim5-ini5,6))

Tempo Verlet:           0.008386
Tempo Velocity Verlet:  0.007095
Tempo RK2:              0.009084
Tempo RK4:              0.014628
